# Goal

The goal of this demo is to demonstrate how the RandomNearIncumbentOptimizer works.

# Method

1. We create a 2-parameter single-objective synthetic function for the BayesianOptimizer to maximize.
2. We either use the pass-through model or train the initial model on a bunch of random parameters.
3. We plot:
    1. The original function
    2. The model's predictions
    3. The utility function values
    
4. We create the RandomNearIncumbentTracer and subscribe to all RandomNearIncumbentOptimizer events.
5. For each call to .suggest():
    1. We capture the initial incumbents and their utility values.
    2. For each call to _run_iteration():
        1. We capture the random neighbors and their utility values.
        2. We capture the new incumbents (and maybe even draw an arrow??)

6. We visualize all the data captured in 5. 

So for each scene we will need:
    1. Optionally the true objective function surface plot.
    2. Predicted value surface plot.
    3. Utility function surface plot.
    4. All past incumbents 3D scatter plot.
    5. All current incumbents 3D scatter plot.
    6. All current neighbors 3D scatter plot.

In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
import math

import mlos.global_values as global_values
from mlos.OptimizerEvaluationTools.ObjectiveFunctionFactory import ObjectiveFunctionFactory, objective_function_config_store
from mlos.OptimizerEvaluationTools.SyntheticFunctions.EnvelopedWaves import EnvelopedWaves, enveloped_waves_config_store
from mlos.Optimizers.BayesianOptimizerFactory import BayesianOptimizerFactory, bayesian_optimizer_config_store
from mlos.Optimizers.ExperimentDesigner.UtilityFunctions.ConfidenceBoundUtilityFunction import ConfidenceBoundUtilityFunction, confidence_bound_utility_function_config_store
from mlos.Optimizers.OptimizationProblem import OptimizationProblem, Objective
from mlos.Spaces import Point
from mlos.Tracer import Tracer
from mlos.Playground.RandomNearIncumbentTracer import RandomNearIncumbentTracer

# Set up the tracer to capture data during execution.
#
global_values.declare_singletons()
global_values.tracer = Tracer(actor_id="demo_notebook")

# Set up the random_near_incumbent_tracer to capture detailed data about it.
#
random_near_incumbent_tracer = RandomNearIncumbentTracer()
global_values.tracer.add_subscriber(event_callback=random_near_incumbent_tracer.add_trace_event)

In [3]:
# Create the objective function and the optimizer.
#
objective_function_config = Point(
    implementation=EnvelopedWaves.__name__,
    enveloped_waves_config=Point(
        num_params=2,
        num_periods=2,
        vertical_shift=0,
        phase_shift=0,
        period=2 * math.pi,
        envelope_type="linear",
        linear_envelope_config=Point(
            gradient=10
        )
    )
)
objective_function = ObjectiveFunctionFactory.create_objective_function(objective_function_config)
optimization_problem = OptimizationProblem(
    parameter_space=objective_function.parameter_space,
    objective_space=objective_function.output_space,
    objectives=[Objective(name='y', minimize=False)]
)
optimizer_config = bayesian_optimizer_config_store.get_config_by_name("default_with_random_near_incumbent_config")
optimizer_config.experiment_designer_config.fraction_random_suggestions = 0.0 # For the purposes of this demo we only want to see guided suggestions.
optimizer_config.homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.n_new_samples_before_refit = 1 # We want the optimizer to be quite responsive.
optimizer_config.experiment_designer_config.utility_function_implementation = ConfidenceBoundUtilityFunction.__name__
optimizer_config.experiment_designer_config.confidence_bound_utility_function_config = confidence_bound_utility_function_config_store.default

optimizer_factory = BayesianOptimizerFactory()
optimizer = optimizer_factory.create_local_optimizer(optimizer_config=optimizer_config, optimization_problem=optimization_problem)

03/15/2021 01:07:51 -   BayesianOptimizerFactory -    INFO - [BayesianOptimizerFactory.py:  40 -    create_local_optimizer() ] Creating a bayesian optimizer with config: {
  "surrogate_model_implementation": "HomogeneousRandomForestRegressionModel",
  "experiment_designer_implementation": "ExperimentDesigner",
  "min_samples_required_for_guided_design_of_experiments": 10,
  "homogeneous_random_forest_regression_model_config.n_estimators": 10,
  "homogeneous_random_forest_regression_model_config.features_fraction_per_estimator": 1,
  "homogeneous_random_forest_regression_model_config.samples_fraction_per_estimator": 0.7,
  "homogeneous_random_forest_regression_model_config.regressor_implementation": "DecisionTreeRegressionModel",
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.criterion": "mse",
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.splitter": "best",
  "homogeneous_random_forest_regression_m

In [4]:
optimizer_config

{
  "surrogate_model_implementation": "HomogeneousRandomForestRegressionModel",
  "experiment_designer_implementation": "ExperimentDesigner",
  "min_samples_required_for_guided_design_of_experiments": 10,
  "homogeneous_random_forest_regression_model_config.n_estimators": 10,
  "homogeneous_random_forest_regression_model_config.features_fraction_per_estimator": 1,
  "homogeneous_random_forest_regression_model_config.samples_fraction_per_estimator": 0.7,
  "homogeneous_random_forest_regression_model_config.regressor_implementation": "DecisionTreeRegressionModel",
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.criterion": "mse",
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.splitter": "best",
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.max_depth": 0,
  "homogeneous_random_forest_regression_model_config.decision_tree_regression_model_config.min_samples_sp

In [5]:
# Let's pre-train the model with some random data
#
random_params_df = objective_function.parameter_space.random_dataframe(100)
random_objectives_df = objective_function.evaluate_dataframe(random_params_df)
optimizer.register(parameter_values_pandas_frame=random_params_df, target_values_pandas_frame=random_objectives_df)

03/15/2021 01:07:54 -   BayesianOptimizerFactory -    INFO - [BayesianOptimizer.py: 153 -                  register() ] Registering 100 parameters and 100 objectives.


In [6]:
import numpy as np
import pandas as pd

# First let's create a meshgrid of the parameters to later use to plot the objective function, the models prediction, and the utility function values.
#
resolution_px = 100
x_0_linspace = objective_function.parameter_space['x_0'].linspace(resolution_px)
x_1_linspace = objective_function.parameter_space['x_1'].linspace(resolution_px)
meshgrids = np.meshgrid(x_0_linspace, x_1_linspace)
reshaped_meshgrids = [meshgrid.reshape(-1) for meshgrid in meshgrids]
meshgrids_dict = {
    dim_name: meshgrid
    for dim_name, meshgrid
    in zip(objective_function.parameter_space.dimension_names, reshaped_meshgrids)
}
meshgrid_params_df = pd.DataFrame(meshgrids_dict)
meshgrid_features_df = optimization_problem.construct_feature_dataframe(parameters_df=meshgrid_params_df, product=True)

In [7]:
# Let's compute the true objectives.
#
true_objectives_df = objective_function.evaluate_dataframe(meshgrid_params_df)
reshaped_true_objectives = true_objectives_df['y'].to_numpy().reshape((resolution_px, resolution_px))

In [31]:
len(random_near_incumbent_tracer.ordered_events)

280

In [35]:
for event in random_near_incumbent_tracer.ordered_events:
    name = event["name"]
    phase = event["phase"]
    args = event["arguments"]
    if name == "RandomNearIncumbentOptimizer._prepare_initial_params_df" and phase == "E":
        print(args['result'])
        break

         x_0        x_1
0   7.259807   7.209334
1   0.827154   2.452285
2   1.071186  12.226734
3   3.201347   4.821146
4   6.403450   7.868766
5   5.297888   8.905332
6   0.844561   3.573101
7  10.910346   4.597949
8   0.324047   8.104125
9   8.163501   0.612971


In [10]:
optimizer.suggest()

03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 165 -                   suggest() ] Suggesting config for context: None
03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 315 - _prepare_initial_params_df() ] Preparing initial params
03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 341 - _prepare_initial_params_df() ] Using 1 of 1 pareto points as starting configs.
03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 359 - _prepare_initial_params_df() ] No cached params are available.
03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 365 - _prepare_initial_params_df() ] Using 9 random points as starting configs.
03/15/2021 01:10:01 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 10/

RandomNearIncumbentOptimizer.suggest B
RandomNearIncumbentOptimizer._prepare_initial_params_df B
RandomNearIncumbentOptimizer._prepare_initial_params_df E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B


03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 116 random neighbors.
03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 60 have positive utility gain.
03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 10 neighbors improved upon their respective incumbents.


RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E


03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 10/10, num neighbors per incumbent: 20
03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 169. Parameter space filtered them down to 169
03/15/2021 01:10:02 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 169 random neighbors.


...

03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 1/10, num neighbors per incumbent: 200
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 200. Parameter space filtered them down to 200
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 200 random neighbors.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 66 have positive utility gain.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 1 neighbors improved upon their respective incumbents.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO 

RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B


03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 200. Parameter space filtered them down to 200
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 200 random neighbors.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 7 have positive utility gain.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 1 neighbors improved upon their respective incumbents.
03/15/2021 01:10:03 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 228 -                   suggest() ] After 9 iterations suggesting: {
  "x_0": 7.575454461213953,
  "x_1": 5.466472482554075
}
03/15/2021 01:10:03 -   Bayesian

RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._cache_good_incumbents B
RandomNearIncumbentOptimizer._cache_good_incumbents E
RandomNearIncumbentOptimizer.suggest E


{
  "x_0": 7.575454461213953,
  "x_1": 5.466472482554075
}

In [12]:
import plotly.graph_objects as go

# Let's find out what the model is predicting.
#
def make_predictions_surface():
    predictions = optimizer.predict(meshgrid_params_df)
    predictions.add_invalid_rows_at_missing_indices(desired_index=meshgrid_params_df.index)
    predictions_df = predictions.get_dataframe()
    reshaped_predictions = predictions_df['predicted_value'].to_numpy().reshape((resolution_px, resolution_px))
    predicted_value_surface = go.Surface(x=x_0_linspace, y=x_1_linspace, z=reshaped_predictions, name="Predicted Values")
    return predicted_value_surface

def make_all_observations_scatterplot():
    params_df, objectives_df, context_df = optimizer.get_all_observations()
    return go.Scatter3d(x=params_df['x_0'], y=params_df['x_1'], z=objectives_df['y'], mode='markers')

def make_utility_function_surface():
    utility_function = optimizer.experiment_designer.utility_function
    computed_utility_values_df = utility_function(meshgrid_features_df.copy(deep=True))
    utility_values_df = pd.DataFrame(columns=['utility'], index=meshgrid_features_df.index)
    utility_values_df['utility'] = 0
    utility_values_df.loc[computed_utility_values_df.index, 'utility'] = computed_utility_values_df['utility']
    reshaped_utility_values = utility_values_df['utility'].to_numpy().reshape((resolution_px, resolution_px))
    utility_value_surface = go.Surface(x=x_0_linspace, y=x_1_linspace, z=reshaped_utility_values, name="Utility Function")
    return utility_value_surface

def make_suggestion_scatterplot(suggested_params, objective_value):
    # We need to compute the utility value for that suggestion.
    #
    utility_function = optimizer.experiment_designer.utility_function
    features_df = optimization_problem.construct_feature_dataframe(parameters_df=suggested_params.to_dataframe())
    utility_value = utility_function(features_df)
    return go.Scatter3d(x=[suggested_params['x_0']], y=[suggested_params['x_1']], z=utility_value['utility'], mode='markers')

objective_function_surface = go.Surface(x=x_0_linspace, y=x_1_linspace, z=reshaped_true_objectives, opacity=0.2, name="True Objective Function Values")

In [58]:
class FrameData:
    """Keeps track of all data for a given frame, and produces plotly traces for that frame.
    
    For each frame we need:
        1. Optionally the true objective function surface plot.
        2. Predicted value surface plot.
        3. Utility function surface plot.
        4. All past incumbents 3D scatter plot.
        5. All current incumbents 3D scatter plot.
        6. All current neighbors 3D scatter plot.
    """
    
    def __init__(
        self,
        utility_values_df: pd.DataFrame = pd.DataFrame(),
        all_observations_df: pd.DataFrame = pd.DataFrame(),
        past_incumbents_df: pd.DataFrame = pd.DataFrame(columns=["x_0", "x_1", "utility"]),
        current_incumbents_df: pd.DataFrame = pd.DataFrame(columns=["x_0", "x_1", "utility"]),
        current_neighbors_df: pd.DataFrame = pd.DataFrame(columns=["x_0", "x_1", "utility"]),
        suggestion_df: pd.DataFrame = pd.DataFrame(columns=["x_0", "x_1", "utility"]),
    ):
        self.utility_values_df = utility_values_df
        self.all_observations_df = all_observations_df
        self.past_incumbents_df = past_incumbents_df
        self.current_incumbents_df = current_incumbents_df
        self.current_neighbors_df = current_neighbors_df
        self.suggestion_df = suggestion_df
        
    def get_frame_data(self):
        # Utility values surface.
        #
        utility_values_df = pd.DataFrame(columns=['utility'], index=meshgrid_features_df.index)
        utility_values_df['utility'] = 0
        utility_values_df.loc[self.utility_values_df.index, 'utility'] = self.utility_values_df['utility']
        reshaped_utility_values = utility_values_df['utility'].to_numpy().reshape((resolution_px, resolution_px))
        utility_value_surface = go.Surface(x=x_0_linspace, y=x_1_linspace, z=reshaped_utility_values, name="Utility Function")
        
        
        all_observations_scatter_plot = go.Scatter3d(x=self.all_observations_df['x_0'], y=self.all_observations_df['x_1'], z=self.all_observations_df['y'], mode='markers', name="all_observations")
        past_incumbents_scatter_plot = go.Scatter3d(x=self.past_incumbents_df['x_0'], y=self.past_incumbents_df['x_1'], z=self.past_incumbents_df['utility'], mode='markers', name="past_incumbents")
        current_incumbents_scatter_plot = go.Scatter3d(x=self.current_incumbents_df['x_0'], y=self.current_incumbents_df['x_1'], z=self.current_incumbents_df['utility'], mode='markers', name="current_incumbents")
        current_neighbors_scatter_plot = go.Scatter3d(x=self.current_neighbors_df['x_0'], y=self.current_neighbors_df['x_1'], z=self.current_neighbors_df['utility'], mode='markers', name="current_neighbors")
        suggestion_scatter_plot = go.Scatter3d(x=self.suggestion_df['x_0'], y=self.suggestion_df['x_1'], z=self.suggestion_df['utility'], mode='markers', name="suggestion")
        
        
        return [
            objective_function_surface,
            utility_value_surface,
            all_observations_scatter_plot,
            past_incumbents_scatter_plot,
            current_incumbents_scatter_plot,
            current_neighbors_scatter_plot,
            suggestion_scatter_plot
        ]
    

In [61]:
# The goal here is to capture raw data needed to prepare traces for each frame.
#
utility_function = optimizer.experiment_designer.utility_function
raw_frames_data = []
num_suggestions = 2
for i in range(num_suggestions):
    
    print(f"[{i}/{num_suggestions}]")
    
    utility_values_df=utility_function(meshgrid_features_df.copy(deep=True))
    params_df, objectives_df, context_df = optimizer.get_all_observations()
    all_observations_df = pd.concat([params_df, objectives_df], axis=1)
    
    pre_suggestion_frame_data = FrameData(
        utility_values_df=utility_values_df,
        all_observations_df=all_observations_df
    )
    raw_frames_data.append(pre_suggestion_frame_data)
    
    random_near_incumbent_tracer.clear_events()
    suggested_params = optimizer.suggest()
    
    # Now we get to iterate over all events in the random_near_incumbent_tracer.ordered_events and produce FrameData objects as appropriate.
    # We keep a little state machine just in case.
    #
    state = None
    for event in random_near_incumbent_tracer.ordered_events:
        name = event["name"]
        phase = event["phase"]
        arguments = event["arguments"]
        
        if name == "RandomNearIncumbentOptimizer._prepare_initial_params_df" and phase == "E":
            # We have initial params in the results object
            current_incumbents_df = arguments["result"]
            features_df = optimization_problem.construct_feature_dataframe(parameters_df=current_incumbents_df.copy())
            utility_df = utility_function(features_df)
            current_incumbents_df['utility'] = utility_df['utility']
            initial_params_frame_data = FrameData(
                utility_values_df=utility_values_df,
                all_observations_df=all_observations_df,
                current_incumbents_df=current_incumbents_df
            )
            raw_frames_data.append(initial_params_frame_data)
            
        if name == "RandomNearIncumbentOptimizer._prepare_random_neighbors" and phase == "E":
            current_neighbors_df = arguments["result"][1]
            features_df = optimization_problem.construct_feature_dataframe(parameters_df=current_neighbors_df.copy())
            utility_df = utility_function(features_df)
            current_neighbors_df['utility'] = utility_df['utility']
            random_neighbors_frame_data = FrameData(
                utility_values_df=utility_values_df,
                all_observations_df=all_observations_df,
                current_incumbents_df=current_incumbents_df,
                current_neighbors_df=current_neighbors_df
            )
        
            
    
    # Compute suggestion_df
    #
    suggestion_features_df = optimization_problem.construct_feature_dataframe(parameters_df=suggested_params.to_dataframe())
    suggestion_utility_value = utility_function(features_df)
    suggestion_df = suggested_params.to_dataframe()
    suggestion_df['utility'] = suggestion_utility_value['utility']
    
    
    
    
    
    
    

[0/2]


03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 165 -                   suggest() ] Suggesting config for context: None
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 315 - _prepare_initial_params_df() ] Preparing initial params
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 341 - _prepare_initial_params_df() ] Using 1 of 1 pareto points as starting configs.
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 354 - _prepare_initial_params_df() ] Using 3 out of 150 cached good configs as starting configs
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 365 - _prepare_initial_params_df() ] Using 6 random points as starting configs.
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ]

RandomNearIncumbentOptimizer.suggest B
RandomNearIncumbentOptimizer._prepare_initial_params_df B
RandomNearIncumbentOptimizer._prepare_initial_params_df E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B


03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 125. Parameter space filtered them down to 125
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 125 random neighbors.
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 40 have positive utility gain.
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 7 neighbors improved upon their respective incumbents.
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 10/10, num neighbors per incumbent: 20
03/15/2021 02:17:55 -   BayesianOptimizerFactory -    INFO 

RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B


...

RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E


03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 2/10, num neighbors per incumbent: 100
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 200. Parameter space filtered them down to 200
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 200 random neighbors.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 12 have positive utility gain.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 2 neighbors improved upon their respective incumbents.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO 

RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B


03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 200. Parameter space filtered them down to 200
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 200 random neighbors.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 13 have positive utility gain.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 1 neighbors improved upon their respective incumbents.
03/15/2021 02:18:00 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 228 -                   suggest() ] After 9 iterations suggesting: {
  "x_0": 7.5611288082738035,
  "x_1": 5.483551522294911
}
03/15/2021 02:18:00 -   Bayesi

RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._cache_good_incumbents B
RandomNearIncumbentOptimizer._cache_good_incumbents E
RandomNearIncumbentOptimizer.suggest E


In [62]:
first_frame = raw_frames_data[0].get_frame_data()

fig = go.Figure(
    data=first_frame,
    frames=[go.Frame(data=frame_data.get_frame_data()) for frame_data in raw_frames_data],
    layout=go.Layout(
        title="Objective Function",
        hovermode="closest",
        #updatemenus=[dict(type="buttons",
        #    buttons=[dict(label="Play",
        #                  method="animate",
        #                  args=[None])])]
        updatemenus=[{
            "buttons":[
                {
                    "args": [None, {"fromcurrent": True}],
                    "label": "Play",
                    "method": "animate"
                },{
                    "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                      "mode": "immediate",
                                      "transition": {"duration": 0}}],
                    "label": "Pause",
                    "method": "animate"
                },{
                    "args": [None, {"fromcurrent": False}],
                    "label": "Restart",
                    "method": "animate"
                },
            ],
            "type":"buttons"
            
        }],
        width=1000,
        height=1000,
        showlegend=True
    )
)

fig.show()

In [16]:
frames_data = []
num_suggestions = 1
for i in range(num_suggestions):
    print(f"[{i}/{num_suggestions}]")
    suggested_params = optimizer.suggest()
    objective_function_value = objective_function.evaluate_point(suggested_params)
    
    frame_data = {
        'utility_function_values_df': 
        'utility_function_surface': make_utility_function_surface(),
        'suggestion_scatter_plot': make_suggestion_scatterplot(suggested_params, objective_function_value),
        'predicted_value_surface': make_predictions_surface(),
        'observations_scatter_plot': make_all_observations_scatterplot()
    }
    frames_data.append(frame_data)
    
    optimizer.register(suggested_params.to_dataframe(), objective_function_value.to_dataframe())
    
    
    
    

03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 165 -                   suggest() ] Suggesting config for context: None
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 315 - _prepare_initial_params_df() ] Preparing initial params
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 341 - _prepare_initial_params_df() ] Using 1 of 1 pareto points as starting configs.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 354 - _prepare_initial_params_df() ] Using 3 out of 10 cached good configs as starting configs
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 365 - _prepare_initial_params_df() ] Using 6 random points as starting configs.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] 

[0/1]
RandomNearIncumbentOptimizer.suggest B
RandomNearIncumbentOptimizer._prepare_initial_params_df B
RandomNearIncumbentOptimizer._prepare_initial_params_df E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B


03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 142 random neighbors.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 47 have positive utility gain.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 7 neighbors improved upon their respective incumbents.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 10/10, num neighbors per incumbent: 20
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 187. Parameter space filtered them down to 187
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO 

RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E


03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 14 have positive utility gain.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 6 neighbors improved upon their respective incumbents.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 10/10, num neighbors per incumbent: 20
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 200. Adapter filtered them down to 194. Parameter space filtered them down to 194
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 194 random neighbors.
03/15/2021 01:11:48 -   BayesianOptimizerFactory -    INFO 

...

03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 239 -            _run_iteration() ] Computed utility for 200 random neighbors.
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 248 -            _run_iteration() ] 27 have positive utility gain.
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 255 -            _run_iteration() ] 9 neighbors improved upon their respective incumbents.
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 418 - _prepare_random_neighbors() ] Num active incumbents: 3/10, num neighbors per incumbent: 66
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 471 - _prepare_random_neighbors() ] Started with 198. Adapter filtered them down to 198. Parameter space filtered them down to 198
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO -

RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E


03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [RandomNearIncumbentOptimizer.py: 228 -                   suggest() ] After 7 iterations suggesting: {
  "x_0": 7.664328263004829,
  "x_1": 5.469990606917021
}
03/15/2021 01:11:49 -   BayesianOptimizerFactory -    INFO - [ExperimentDesigner.py: 189 -                   suggest() ] Produced a guided suggestion: {
  "x_0": 7.664328263004829,
  "x_1": 5.469990606917021
}


RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._cache_good_incumbents B
RandomNearIncumbentOptimizer._cache_good_incumbents E
RandomNearIncumbentOptimizer.suggest E


03/15/2021 01:11:50 -   BayesianOptimizerFactory -    INFO - [BayesianOptimizer.py: 153 -                  register() ] Registering 1 parameters and 1 objectives.


In [23]:
for event in random_near_incumbent_tracer.ordered_events:
    print(event["name"], event["phase"])
    if event["name"] == "RandomNearIncumbentOptimizer._prepare_initial_params_df" and event["phase"] == "E":
        print(event["arguments"])

RandomNearIncumbentOptimizer.suggest B
RandomNearIncumbentOptimizer._prepare_initial_params_df B
RandomNearIncumbentOptimizer._prepare_initial_params_df E
{'result':          x_0        x_1
0   7.259807   7.209334
1   0.827154   2.452285
2   1.071186  12.226734
3   3.201347   4.821146
4   6.403450   7.868766
5   5.297888   8.905332
6   0.844561   3.573101
7  10.910346   4.597949
8   0.324047   8.104125
9   8.163501   0.612971}
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptimizer._prepare_random_neighbors E
RandomNearIncumbentOptimizer._compute_utility_for_params B
RandomNearIncumbentOptimizer._compute_utility_for_params E
RandomNearIncumbentOptimizer._run_iteration E
RandomNearIncumbentOptimizer._run_iteration B
RandomNearIncumbentOptimizer._prepare_random_neighbors B
RandomNearIncumbentOptim

In [ ]:
frames_data[0]['observations_scatter_plot']

In [ ]:
first_frame = [objective_function_surface, frames_data[0]['utility_function_surface'], frames_data[0]['suggestion_scatter_plot'], frames_data[0]['observations_scatter_plot']]

fig = go.Figure(
    data=first_frame,
    frames=[go.Frame(data=[objective_function_surface, frame_data['utility_function_surface'], frame_data['suggestion_scatter_plot'], frame_data['observations_scatter_plot']]) for frame_data in frames_data],
    layout=go.Layout(
        title="Objective Function",
        hovermode="closest",
        #updatemenus=[dict(type="buttons",
        #    buttons=[dict(label="Play",
        #                  method="animate",
        #                  args=[None])])]
        updatemenus=[{
            "buttons":[
                {
                    "args": [None, {"fromcurrent": True}],
                    "label": "Play",
                    "method": "animate"
                },{
                    "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                      "mode": "immediate",
                                      "transition": {"duration": 0}}],
                    "label": "Pause",
                    "method": "animate"
                },{
                    "args": [None, {"fromcurrent": False}],
                    "label": "Restart",
                    "method": "animate"
                },
            ],
            "type":"buttons"
            
        }],
        width=1000,
        height=1000,
        showlegend=True
    )
)

fig.show()

In [17]:
last_frame = [objective_function_surface, frames_data[-1]['predicted_value_surface'], frames_data[-1]['observations_scatter_plot']]

fig = go.Figure(
    data=last_frame,
    layout=go.Layout(
        title="Objective Function",
        hovermode="closest",
        updatemenus=[
            {
                "buttons": [
                {
                    "args": [None, {"frame": {"duration": 500, "redraw": False},
                                    "fromcurrent": True, "transition": {"duration": 300,
                                                                        "easing": "quadratic-in-out"}}],
                    "label": "Play",
                    "method": "animate"
                },
                {
                    "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                      "mode": "immediate",
                                      "transition": {"duration": 0}}],
                    "label": "Pause",
                    "method": "animate"
                }
                ]
            }
        ],
        width=1000,
        height=1000,
        showlegend=True
    )
)

fig.show()